In [ ]:
!pip install contractions

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 289.9/289.9 kB 6.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.7/110.7 kB 3.9 MB/s eta 0:00:00


In [ ]:
import pandas as pd
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
import string
import re
from nltk.stem import PorterStemmer,WordNetLemmatizer
from nltk.tokenize import regexp_tokenize
import contractions
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import classification_report, accuracy_score,precision_score,recall_score,confusion_matrix
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import MultinomialNB
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
import numpy as np
import pandas as pd
import gensim
from gensim.models import Word2Vec
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense
from tensorflow.keras.optimizers import Adam
from sklearn.model_selection import train_test_split

In [ ]:
pip show tensorflow

Name: tensorflow
Version: 2.17.0
Summary: TensorFlow is an open source machine learning framework for everyone.
Home-page: https://www.tensorflow.org/
Author: Google Inc.
Author-email: packages@tensorflow.org
License: Apache 2.0
Location: /usr/local/lib/python3.10/dist-packages
Requires: absl-py, astunparse, flatbuffers, gast, google-pasta, grpcio, h5py, keras, libclang, ml-dtypes, numpy, opt-einsum, packaging, protobuf, requests, setuptools, six, tensorboard, tensorflow-io-gcs-filesystem, termcolor, typing-extensions, wrapt
Required-by: dopamine_rl, tf_keras


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
nlp_df=pd.read_csv("/content/drive/MyDrive/Bank Risk Controller/NLP_Project/training.1600000.processed.noemoticon.csv",
                   encoding='ISO-8859-1',header=None,names=['Target', 'ID', 'Date', 'Flag', 'User', 'Text'])


In [ ]:
nlp_df.head()

Target          ID                          Date      Flag  \
0       0  1467810369  Mon Apr 06 22:19:45 PDT 2009  NO_QUERY   
1       0  1467810672  Mon Apr 06 22:19:49 PDT 2009  NO_QUERY   
2       0  1467810917  Mon Apr 06 22:19:53 PDT 2009  NO_QUERY   
3       0  1467811184  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   
4       0  1467811193  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   

              User                                               Text  
0  _TheSpecialOne_  @switchfoot http://twitpic.com/2y1zl - Awww, t...  
1    scotthamilton  is upset that he can't update his Facebook by ...  
2         mattycus  @Kenichan I dived many times for the ball. Man...  
3          ElleCTF    my whole body feels itchy and like its on fire   
4           Karoli  @nationwideclass no, it's not behaving at all....

In [ ]:
nlp_df.shape

(1600000, 6)

In [ ]:
nlp_df.isna().sum()

Target    0
ID        0
Date      0
Flag      0
User      0
Text      0
dtype: int64

In [ ]:
nlp_df['Target'].value_counts()

Target
0    800000
4    800000
Name: count, dtype: int64

## Starting the Text Preprocessing

In [ ]:
# Download necessary resources
nltk.download('stopwords')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
# Set display options to show the full content of text fields
pd.set_option('display.max_colwidth', None)

In [ ]:
nlp_df['Text'][0:3]

0    @switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D
1        is upset that he can't update his Facebook by texting it... and might cry as a result  School today also. Blah!
2                              @Kenichan I dived many times for the ball. Managed to save 50%  The rest go out of bounds
Name: Text, dtype: object

In [ ]:
# Test the contraction expansion
test_text = "I can't believe it. David Carr should've been in the game."
expanded_text = contractions.fix(test_text)
print(expanded_text)  # Expected

I cannot believe it. David Carr should have been in the game.


In [ ]:
def expand_contractions(text):
    return contractions.fix(text)

def preprocess_text(text):

    # Convert to lowercase
    text = text.lower()
    # Remove user mentions
    text = re.sub(r'@\w+', '', text)
    # print("text after the user mentions removal : ",text)
    #Remove all the special characters except for apostrophes
    text = re.sub(r'[^a-zA-Z0-9\'\s]', '', text)
    # Expand contractions
    text = expand_contractions(text)
    # print("Text after contraction expansion :",text)
    # Remove URLs
    text = re.sub(r'http\S+|www\S+|https\S+', '', text, flags=re.MULTILINE)
    # print("Text after URL removal : ",text)
    # Custom tokenization to keep contractions intact
    pattern = r"\b\w+'\w+|\b\w+|[^\w\s]"
    tokens = regexp_tokenize(text, pattern)
    # print("Tokens after custom tokenization:", tokens)
    # Remove stop words
    stop_words = set(stopwords.words('english'))
    tokens = [word for word in tokens if word not in stop_words]
    #Remove special characters
    tokens=[word for word in tokens if word.isalnum()]
    # print("text after stop word removal :", tokens)

    return ' '.join(tokens)

In [ ]:
nlp_df[nlp_df['Target']==0]

Target          ID                          Date      Flag  \
0            0  1467810369  Mon Apr 06 22:19:45 PDT 2009  NO_QUERY   
1            0  1467810672  Mon Apr 06 22:19:49 PDT 2009  NO_QUERY   
2            0  1467810917  Mon Apr 06 22:19:53 PDT 2009  NO_QUERY   
3            0  1467811184  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   
4            0  1467811193  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   
...        ...         ...                           ...       ...   
799995       0  2329205009  Thu Jun 25 10:28:28 PDT 2009  NO_QUERY   
799996       0  2329205038  Thu Jun 25 10:28:28 PDT 2009  NO_QUERY   
799997       0  2329205473  Thu Jun 25 10:28:30 PDT 2009  NO_QUERY   
799998       0  2329205574  Thu Jun 25 10:28:30 PDT 2009  NO_QUERY   
799999       0  2329205794  Thu Jun 25 10:28:31 PDT 2009  NO_QUERY   

                   User  \
0       _TheSpecialOne_   
1         scotthamilton   
2              mattycus   
3               ElleCTF   
4                Karoli   
...                 ...   
799995         dandykim   
799996          bigenya   
799997         LeeLHoke   
799998     davidlmulder   
799999       tpchandler   

                                                                                                                       Text  
0       @switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D  
1           is upset that he can't update his Facebook by texting it... and might cry as a result  School today also. Blah!  
2                                 @Kenichan I dived many times for the ball. Managed to save 50%  The rest go out of bounds  
3                                                                           my whole body feels itchy and like its on fire   
4           @nationwideclass no, it's not behaving at all. i'm mad. why am i here? because I can't see you all over there.   
...                                                                                                                     ...  
799995                                                      Sick  Spending my day laying in bed listening to @taylorswift13  
799996                                                                                                      Gmail is down?   
799997                                                                                        rest in peace Farrah! So sad   
799998                        @Eric_Urbane Sounds like a rival is flagging your ads. Not much you can do about that though   
799999                                   has to resit exams over summer...  wishes he worked harder at first year of uni...  

[800000 rows x 6 columns]

In [ ]:
for text in nlp_df['Text'][20:25]:
    print("Text before processing : ",text)
    final_text=preprocess_text(text)
    print("Text after processing :",final_text)
    print("\n")

Text before processing :  @alydesigns i was out most of the day so didn't get much done 
Text after processing : day get much done


Text before processing :  one of my friend called me, and asked to meet with her at Mid Valley today...but i've no time *sigh* 
Text after processing : one friend called asked meet mid valley todaybut time sigh


Text before processing :  @angry_barista I baked you a cake but I ated it 
Text after processing : baked cake ated


Text before processing :  this week is not going as i had hoped 
Text after processing : week going hoped


Text before processing :  blagh class at 8 tomorrow 
Text after processing : blagh class 8 tomorrow




In [ ]:
nlp_df.head()

Target          ID                          Date      Flag  \
0       0  1467810369  Mon Apr 06 22:19:45 PDT 2009  NO_QUERY   
1       0  1467810672  Mon Apr 06 22:19:49 PDT 2009  NO_QUERY   
2       0  1467810917  Mon Apr 06 22:19:53 PDT 2009  NO_QUERY   
3       0  1467811184  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   
4       0  1467811193  Mon Apr 06 22:19:57 PDT 2009  NO_QUERY   

              User  \
0  _TheSpecialOne_   
1    scotthamilton   
2         mattycus   
3          ElleCTF   
4           Karoli   

                                                                                                                  Text  
0  @switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D  
1      is upset that he can't update his Facebook by texting it... and might cry as a result  School today also. Blah!  
2                            @Kenichan I dived many times for the ball. Managed to save 50%  The rest go out of bounds  
3                                                                      my whole body feels itchy and like its on fire   
4      @nationwideclass no, it's not behaving at all. i'm mad. why am i here? because I can't see you all over there.

In [ ]:
nlp_df['Text_Processed'] = nlp_df['Text'].apply(preprocess_text)

In [ ]:
nlp_df[['Text','Text_Processed']][0:10]

Text  \
0  @switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D   
1      is upset that he can't update his Facebook by texting it... and might cry as a result  School today also. Blah!   
2                            @Kenichan I dived many times for the ball. Managed to save 50%  The rest go out of bounds   
3                                                                      my whole body feels itchy and like its on fire    
4      @nationwideclass no, it's not behaving at all. i'm mad. why am i here? because I can't see you all over there.    
5                                                                                        @Kwesidei not the whole crew    
6                                                                                                          Need a hug    
7                  @LOLTrish hey  long time no see! Yes.. Rains a bit ,only a bit  LOL , I'm fine thanks , how's you ?   
8                                                                                 @Tatiana_K nope they didn't have it    
9                                                                                            @twittera que me muera ?    

                                                                 Text_Processed  
0                                  awww bummer shoulda got david carr third day  
1  upset cannot update facebook texting might cry result school today also blah  
2                          dived many times ball managed save 50 rest go bounds  
3                                              whole body feels itchy like fire  
4                                                       behaving mad cannot see  
5                                                                    whole crew  
6                                                                      need hug  
7                           hey long time see yes rains bit bit lol fine thanks  
8                                                                          nope  
9                                                                     que muera

In [ ]:
stemmer = PorterStemmer()
lemmatizer = WordNetLemmatizer()

def stem_text(text):
    tokens = word_tokenize(text)
    return ' '.join([stemmer.stem(token) for token in tokens])

def lemmatize_text(text):
    tokens = word_tokenize(text)
    return ' '.join([lemmatizer.lemmatize(token) for token in tokens])

In [ ]:
nlp_df['Text_Processed_stem'] = nlp_df['Text_Processed'].apply(stem_text)

In [ ]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /root/nltk_data...


True

In [ ]:
nlp_df['Text_Processed_lemma'] = nlp_df['Text_Processed'].apply(lemmatize_text)

In [ ]:
nlp_df[['Text','Text_Processed','Text_Processed_stem','Text_Processed_lemma']][0:10]

Text  \
0  @switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D   
1      is upset that he can't update his Facebook by texting it... and might cry as a result  School today also. Blah!   
2                            @Kenichan I dived many times for the ball. Managed to save 50%  The rest go out of bounds   
3                                                                      my whole body feels itchy and like its on fire    
4      @nationwideclass no, it's not behaving at all. i'm mad. why am i here? because I can't see you all over there.    
5                                                                                        @Kwesidei not the whole crew    
6                                                                                                          Need a hug    
7                  @LOLTrish hey  long time no see! Yes.. Rains a bit ,only a bit  LOL , I'm fine thanks , how's you ?   
8                                                                                 @Tatiana_K nope they didn't have it    
9                                                                                            @twittera que me muera ?    

                                                                 Text_Processed  \
0                                  awww bummer shoulda got david carr third day   
1  upset cannot update facebook texting might cry result school today also blah   
2                          dived many times ball managed save 50 rest go bounds   
3                                              whole body feels itchy like fire   
4                                                       behaving mad cannot see   
5                                                                    whole crew   
6                                                                      need hug   
7                           hey long time see yes rains bit bit lol fine thanks   
8                                                                          nope   
9                                                                     que muera   

                                                         Text_Processed_stem  \
0                               awww bummer shoulda got david carr third day   
1  upset can not updat facebook text might cri result school today also blah   
2                            dive mani time ball manag save 50 rest go bound   
3                                            whole bodi feel itchi like fire   
4                                                      behav mad can not see   
5                                                                 whole crew   
6                                                                   need hug   
7                           hey long time see ye rain bit bit lol fine thank   
8                                                                       nope   
9                                                                  que muera   

                                                            Text_Processed_lemma  
0                                   awww bummer shoulda got david carr third day  
1  upset can not update facebook texting might cry result school today also blah  
2                             dived many time ball managed save 50 rest go bound  
3                                                whole body feel itchy like fire  
4                                                       behaving mad can not see  
5                                                                     whole crew  
6                                                                       need hug  
7                             hey long time see yes rain bit bit lol fine thanks  
8                                                                           nope  
9                                                                      que muera

In [ ]:
nlp_df[['Text','Text_Processed','Text_Processed_lemma']][0:10]

Text  \
0  @switchfoot http://twitpic.com/2y1zl - Awww, that's a bummer.  You shoulda got David Carr of Third Day to do it. ;D   
1      is upset that he can't update his Facebook by texting it... and might cry as a result  School today also. Blah!   
2                            @Kenichan I dived many times for the ball. Managed to save 50%  The rest go out of bounds   
3                                                                      my whole body feels itchy and like its on fire    
4      @nationwideclass no, it's not behaving at all. i'm mad. why am i here? because I can't see you all over there.    
5                                                                                        @Kwesidei not the whole crew    
6                                                                                                          Need a hug    
7                  @LOLTrish hey  long time no see! Yes.. Rains a bit ,only a bit  LOL , I'm fine thanks , how's you ?   
8                                                                                 @Tatiana_K nope they didn't have it    
9                                                                                            @twittera que me muera ?    

                                                                 Text_Processed  \
0                                  awww bummer shoulda got david carr third day   
1  upset cannot update facebook texting might cry result school today also blah   
2                          dived many times ball managed save 50 rest go bounds   
3                                              whole body feels itchy like fire   
4                                                       behaving mad cannot see   
5                                                                    whole crew   
6                                                                      need hug   
7                           hey long time see yes rains bit bit lol fine thanks   
8                                                                          nope   
9                                                                     que muera   

                                                            Text_Processed_lemma  
0                                   awww bummer shoulda got david carr third day  
1  upset can not update facebook texting might cry result school today also blah  
2                             dived many time ball managed save 50 rest go bound  
3                                                whole body feel itchy like fire  
4                                                       behaving mad can not see  
5                                                                     whole crew  
6                                                                       need hug  
7                             hey long time see yes rain bit bit lol fine thanks  
8                                                                           nope  
9                                                                      que muera

In [ ]:
nlp_df.to_csv('/content/drive/MyDrive/Bank Risk Controller/NLP_Project/nlp_preprocessed_sentiment_data.csv',index=False)

## Checking the model performance with Lemmatization with user defined Word2Vec

In [ ]:
# Tokenization
tokenizer = Tokenizer()
tokenizer.fit_on_texts(nlp_df['Text_Processed_lemma'])
word_index = tokenizer.word_index
sequences = tokenizer.texts_to_sequences(nlp_df['Text_Processed_lemma'])

In [ ]:
import pickle

# Assume 'tokenizer' is your Tokenizer object
with open('/content/drive/MyDrive/Bank Risk Controller/NLP_Project/Model output/sentiment_analysis_iter2_tokenizer.pkl', 'wb') as file:
    pickle.dump(tokenizer, file)

In [ ]:
print(word_index)## It is a dictionary which provides a number for each of the words

{'day': 1, 'good': 2, 'going': 3, 'get': 4, 'like': 5, 'go': 6, 'got': 7, 'love': 8, 'work': 9, 'can': 10, 'not': 11, 'today': 12, 'want': 13, 'time': 14, 'know': 15, 'back': 16, 'one': 17, 'lol': 18, 'really': 19, 'see': 20, 'think': 21, 'night': 22, 'still': 23, 'would': 24, 'thanks': 25, 'new': 26, 'well': 27, 'amp': 28, 'need': 29, 'home': 30, 'oh': 31, '2': 32, 'miss': 33, 'much': 34, 'last': 35, 'feel': 36, 'make': 37, 'tomorrow': 38, 'hope': 39, 'morning': 40, 'great': 41, 'twitter': 42, 'though': 43, 'haha': 44, 'wish': 45, 'way': 46, 'sad': 47, 'could': 48, 'come': 49, 'fun': 50, 'right': 51, 'sleep': 52, 'week': 53, 'bad': 54, 'happy': 55, 'thing': 56, 'sorry': 57, 'tonight': 58, 'friend': 59, 'getting': 60, 'people': 61, 'look': 62, 'nice': 63, 'better': 64, 'watching': 65, 'say': 66, 'wait': 67, 'hate': 68, 'bed': 69, 'yeah': 70, 'hour': 71, 'school': 72, 'u': 73, 'guy': 74, 'yes': 75, 'weekend': 76, 'even': 77, 'hey': 78, 'take': 79, 'next': 80, 'show': 81, 'soon': 82, 'aw

In [ ]:
print(len(word_index))

412513


In [ ]:
print(type(sequences))
print(sequences[0:4])

<class 'list'>
[[340, 1028, 3154, 7, 701, 8871, 1665, 1], [613, 10, 11, 271, 420, 1830, 184, 269, 956, 72, 12, 167, 1021], [62873, 204, 14, 833, 1445, 715, 1105, 345, 6, 2901], [309, 644, 36, 2646, 5, 961]]


In [ ]:
# Padding sequences
max_sequence_length = max(len(seq) for seq in sequences)
X_pad = pad_sequences(sequences, maxlen=max_sequence_length)

In [ ]:
print(max_sequence_length)

34


In [ ]:
print(type(X_pad))

<class 'numpy.ndarray'>


In [ ]:
X_pad[0]

array([   0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
          0,    0,    0,    0,  340, 1028, 3154,    7,  701, 8871, 1665,
          1], dtype=int32)

In [ ]:
# Define target labels
y = nlp_df['Target']

In [ ]:
y=y.map({0:0,4:1})

In [ ]:
# Train-test split
X_train, X_test, y_train, y_test = train_test_split(X_pad, y, test_size=0.2, random_state=42)

In [ ]:
print(X_train.shape)
print(y_train.shape)
print(y_train.value_counts())
print(X_test.shape)
print(y_test.shape)
print(y_test.value_counts())

(1280000, 34)
(1280000,)
Target
0    640506
1    639494
Name: count, dtype: int64
(320000, 34)
(320000,)
Target
1    160506
0    159494
Name: count, dtype: int64


In [ ]:
# Train Word2Vec model
sentences = [text.split() for text in nlp_df['Text_Processed_lemma']]
word2vec_model = Word2Vec(sentences, vector_size=300, window=5, min_count=1, sg=0)

In [ ]:
## using the Google's pre-trained word2vec model
from gensim.models import KeyedVectors

# Load the pre-trained Word2Vec model from Google Drive
model_path = '/content/drive/MyDrive/GoogleNews-vectors-negative300.bin.gz'
word2vec_model = KeyedVectors.load_word2vec_format(model_path, binary=True)

In [ ]:
# Create embedding matrix
embedding_dim = 300
embedding_matrix = np.zeros((len(word_index) + 1, embedding_dim))
for word, i in word_index.items():
    if word in word2vec_model.wv:
        embedding_matrix[i] = word2vec_model.wv[word]

In [ ]:
## embedding matrix if using the pre-trained models.
embedding_dim = 300
embedding_matrix = np.zeros((len(word_index) + 1, embedding_dim))
for word, i in word_index.items():
    if word in word2vec_model:
        embedding_matrix[i] = word2vec_model[word]
    else:
        # Option 1: Random Initialization
        embedding_matrix[i] = np.random.normal(scale=0.6, size=(embedding_dim,))

In [ ]:
print(embedding_matrix.shape)
print(embedding_matrix[10])

(412514, 300)
[ 4.87000555e-01  1.14364810e-01 -4.70429808e-01  1.19512558e+00
 -2.98459202e-01  7.11476684e-01 -6.74666226e-01 -9.57937896e-01
  9.85011935e-01  2.61512697e-01 -4.74558502e-01 -1.73942924e+00
 -3.78064334e-01  4.58032757e-01  1.08115923e+00 -1.24015844e+00
  2.40902925e+00 -1.03593469e-01  1.38123167e+00  1.61088252e+00
  1.94862142e-01 -4.36938465e-01  1.59547284e-01  5.28883934e-01
  2.17969990e+00 -5.99320889e-01  7.37618729e-02 -6.59797907e-01
 -1.17533541e+00  1.03373162e-01  1.79999650e-01 -1.11020958e+00
 -7.22283065e-01 -3.68845582e-01 -9.98733580e-01 -1.43372762e+00
 -4.10521209e-01  2.00203037e+00  8.77487719e-01 -2.41983795e+00
 -3.35699111e-01  2.90625334e-01 -1.96549907e-01  5.19907236e-01
 -2.96225739e+00  5.43366671e-01 -9.42895889e-01 -1.49656188e+00
 -1.35616207e+00  1.84848964e+00  7.79879808e-01 -3.23239088e-01
 -1.10928309e+00 -1.87818694e+00  1.01746202e+00  4.04194027e-01
  2.09911513e+00  1.32066047e+00 -1.96983725e-01 -5.28476000e-01
  3.0696950

In [ ]:
y_train.value_counts()

Target
0    640506
1    639494
Name: count, dtype: int64

In [ ]:
from tensorflow.keras.layers import SimpleRNN

def create_rnn_model():
    model = Sequential()
    model.add(Embedding(input_dim=len(word_index) + 1, output_dim=embedding_dim, weights=[embedding_matrix], input_length=max_sequence_length, trainable=False))
    model.add(SimpleRNN(64, return_sequences=False))  # RNN layer
    model.add(Dense(1, activation='sigmoid'))  # Output layer for binary classification
    model.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])
    return model


In [ ]:
# Create and train the RNN model
rnn_model = create_rnn_model()
rnn_model.summary()


/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


Model: "sequential_6"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ embedding_6 (Embedding)              │ ?                           │     123,754,200 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ simple_rnn (SimpleRNN)               │ ?                           │     0 (unbuilt) │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_12 (Dense)                     │ ?                           │     0 (unbuilt) │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 123,754,200 (472.08 MB)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 123,754,200 (472.08 MB)

In [ ]:
rnn_model.fit(X_train, y_train, epochs=5, batch_size=64, validation_split=0.2, verbose=1)

Epoch 1/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 294s 18ms/step - accuracy: 0.7331 - loss: 0.5266 - val_accuracy: 0.7577 - val_loss: 0.4924
Epoch 2/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 323s 18ms/step - accuracy: 0.7650 - loss: 0.4840 - val_accuracy: 0.7620 - val_loss: 0.4918
Epoch 3/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 336s 19ms/step - accuracy: 0.7663 - loss: 0.4832 - val_accuracy: 0.7671 - val_loss: 0.4811
Epoch 4/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 305s 18ms/step - accuracy: 0.7687 - loss: 0.4797 - val_accuracy: 0.7701 - val_loss: 0.4794
Epoch 5/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 292s 18ms/step - accuracy: 0.7712 - loss: 0.4742 - val_accuracy: 0.7703 - val_loss: 0.4765


In [ ]:
y_pred_prob=rnn_model.predict(X_test,batch_size=64)

5000/5000 ━━━━━━━━━━━━━━━━━━━━ 48s 9ms/step


In [ ]:
# Convert probabilities to class labels (0 or 1)
y_pred = (y_pred_prob > 0.5).astype(int)

In [ ]:
y_test.shape

(320000,)

In [ ]:
y_test.values.ravel()

array([0, 0, 0, ..., 1, 1, 0])

In [ ]:
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix

# Ensure y_test is in correct shape
y_test = y_test.values.ravel()

# Print the classification report
print("Classification Report:")
print(classification_report(y_test, y_pred))

# Print the accuracy score
print("Accuracy Score:")
print(accuracy_score(y_test, y_pred))

# Print the confusion matrix
print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))

Classification Report:
              precision    recall  f1-score   support

           0       0.77      0.77      0.77    159494
           1       0.77      0.77      0.77    160506

    accuracy                           0.77    320000
   macro avg       0.77      0.77      0.77    320000
weighted avg       0.77      0.77      0.77    320000

Accuracy Score:
0.77054375
Confusion Matrix:
[[123415  36079]
 [ 37347 123159]]


In [ ]:
# Save the model
rnn_model.save('/content/drive/MyDrive/Bank Risk Controller/NLP_Project/Model output/sentiment_analysis_iter2_rnn_model.h5')

In [ ]:
## Saving in the latest format as suggested
rnn_model.save('/content/drive/MyDrive/Bank Risk Controller/NLP_Project/Model output/sentiment_analysis_iter2_rnn_model.keras')

## Building the LSTM Model

In [ ]:
from tensorflow.keras.layers import LSTM

def create_lstm_model():
    model = Sequential()
    model.add(Embedding(input_dim=len(word_index) + 1, output_dim=embedding_dim, weights=[embedding_matrix], input_length=max_sequence_length, trainable=False))
    model.add(LSTM(64, return_sequences=False))  # LSTM layer
    model.add(Dense(1, activation='sigmoid'))  # Output layer for binary classification
    model.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])
    return model

In [ ]:
# Create and train the LSTM model
lstm_model = create_lstm_model()
lstm_model.summary()

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


Model: "sequential_7"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ embedding_7 (Embedding)              │ ?                           │     123,754,200 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm (LSTM)                          │ ?                           │     0 (unbuilt) │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_13 (Dense)                     │ ?                           │     0 (unbuilt) │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 123,754,200 (472.08 MB)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 123,754,200 (472.08 MB)

In [ ]:
lstm_model.fit(X_train, y_train, epochs=5, batch_size=64, validation_split=0.2, verbose=1)

Epoch 1/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 905s 56ms/step - accuracy: 0.7615 - loss: 0.4865 - val_accuracy: 0.7798 - val_loss: 0.4602
Epoch 2/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 981s 60ms/step - accuracy: 0.7859 - loss: 0.4494 - val_accuracy: 0.7826 - val_loss: 0.4559
Epoch 3/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 921s 56ms/step - accuracy: 0.7910 - loss: 0.4404 - val_accuracy: 0.7857 - val_loss: 0.4498
Epoch 4/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 922s 56ms/step - accuracy: 0.7947 - loss: 0.4346 - val_accuracy: 0.7869 - val_loss: 0.4490
Epoch 5/5
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 971s 61ms/step - accuracy: 0.7975 - loss: 0.4298 - val_accuracy: 0.7859 - val_loss: 0.4500


In [ ]:
## Saving in the latest format as suggested
lstm_model.save('/content/drive/MyDrive/Bank Risk Controller/NLP_Project/Model output/sentiment_analysis_iter2_lstm_model.keras')

In [ ]:
y_pred_prob=lstm_model.predict(X_test,batch_size=64)

5000/5000 ━━━━━━━━━━━━━━━━━━━━ 132s 26ms/step


In [ ]:
# Convert probabilities to class labels (0 or 1)
y_pred = (y_pred_prob > 0.5).astype(int)

In [ ]:
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix

# Ensure y_test is in correct shape
# y_test = y_test.values.ravel()

# Print the classification report
print("Classification Report:")
print(classification_report(y_test, y_pred))

# Print the accuracy score
print("Accuracy Score:")
print(accuracy_score(y_test, y_pred))

# Print the confusion matrix
print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))

Classification Report:
              precision    recall  f1-score   support

           0       0.80      0.76      0.78    159494
           1       0.77      0.81      0.79    160506

    accuracy                           0.79    320000
   macro avg       0.79      0.79      0.79    320000
weighted avg       0.79      0.79      0.79    320000

Accuracy Score:
0.7868375
Confusion Matrix:
[[121132  38362]
 [ 29850 130656]]


# Building the LSTM Model with Google's pre-trained word2vec

In [ ]:
from tensorflow.keras.layers import LSTM

def create_lstm_model():
    model = Sequential()
    model.add(Embedding(input_dim=len(word_index) + 1, output_dim=embedding_dim, weights=[embedding_matrix], input_length=max_sequence_length, trainable=False))
    model.add(LSTM(64, return_sequences=False))  # LSTM layer
    model.add(Dense(1, activation='sigmoid'))  # Output layer for binary classification
    model.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])
    return model

In [ ]:
# Create and train the LSTM model
lstm_model = create_lstm_model()
lstm_model.summary()

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ embedding (Embedding)                │ ?                           │     123,754,200 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm (LSTM)                          │ ?                           │     0 (unbuilt) │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ ?                           │     0 (unbuilt) │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 123,754,200 (472.08 MB)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 123,754,200 (472.08 MB)

In [ ]:
lstm_model.fit(X_train, y_train, epochs=8, batch_size=64, validation_split=0.2, verbose=1)

Epoch 1/8
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 887s 55ms/step - accuracy: 0.7400 - loss: 0.5180 - val_accuracy: 0.7735 - val_loss: 0.4689
Epoch 2/8
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 864s 52ms/step - accuracy: 0.7819 - loss: 0.4570 - val_accuracy: 0.7794 - val_loss: 0.4604
Epoch 3/8
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 867s 52ms/step - accuracy: 0.7930 - loss: 0.4390 - val_accuracy: 0.7818 - val_loss: 0.4598
Epoch 4/8
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 866s 52ms/step - accuracy: 0.8025 - loss: 0.4239 - val_accuracy: 0.7819 - val_loss: 0.4601
Epoch 5/8
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 826s 52ms/step - accuracy: 0.8070 - loss: 0.4146 - val_accuracy: 0.7793 - val_loss: 0.4656
Epoch 6/8
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 872s 52ms/step - accuracy: 0.8124 - loss: 0.4062 - val_accuracy: 0.7799 - val_loss: 0.4660
Epoch 7/8
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 839s 52ms/step - accuracy: 0.8163 - loss: 0.4002 - val_accuracy: 0.7801 - val_loss: 0.4711
Epoch 8/8
16000/16000 ━━━━━━━━━━━━━━━━━━━━ 921s 56ms/step - ac

In [ ]:
## Saving in the latest format as suggested
lstm_model.save('/content/drive/MyDrive/Bank Risk Controller/NLP_Project/Model output/sentiment_analysis_iter2_lstm_model2.keras')

In [ ]:
y_pred_prob=lstm_model.predict(X_test,batch_size=64)

5000/5000 ━━━━━━━━━━━━━━━━━━━━ 112s 22ms/step


In [ ]:
y_pred_prob

array([[0.05769194],
       [0.97401285],
       [0.773847  ],
       ...,
       [0.99168324],
       [0.20849773],
       [0.10079341]], dtype=float32)

In [ ]:
# Convert probabilities to class labels (0 or 1)
y_pred = (y_pred_prob > 0.5).astype(int)

In [ ]:
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix

# Ensure y_test is in correct shape
# y_test = y_test.values.ravel()

# Print the classification report
print("Classification Report:")
print(classification_report(y_test, y_pred))

# Print the accuracy score
print("Accuracy Score:")
print(accuracy_score(y_test, y_pred))

# Print the confusion matrix
print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))

Classification Report:
              precision    recall  f1-score   support

           0       0.78      0.77      0.78    159494
           1       0.77      0.79      0.78    160506

    accuracy                           0.78    320000
   macro avg       0.78      0.78      0.78    320000
weighted avg       0.78      0.78      0.78    320000

Accuracy Score:
0.778109375
Confusion Matrix:
[[122838  36656]
 [ 34349 126157]]


## Try this next

In [ ]:
def create_lstm_model():
    model = Sequential()
    model.add(Embedding(input_dim=len(word_index) + 1, output_dim=embedding_dim, weights=[embedding_matrix], input_length=max_sequence_length, trainable=False))
    model.add(LSTM(128, return_sequences=True))  # First LSTM layer with 128 nodes
    model.add(LSTM(64, return_sequences=True))   # Second LSTM layer with 64 nodes
    model.add(LSTM(32, return_sequences=False))  # Third LSTM layer with 32 nodes
    model.add(Dense(1, activation='sigmoid'))    # Output layer for binary classification
    model.compile(optimizer=Adam(), loss='binary_crossentropy', metrics=['accuracy'])
    return model
